<a href="https://colab.research.google.com/github/Motolover/Web_analytics/blob/main/parser_new_V4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Установка общих либ и запуск основного скрипта парсинга: https://www.joytoy.com


In [2]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import re
import lxml

In [66]:
import json

In [3]:
input_url = input("Необходимо указать заглавную страницу товарной категории: ")

text = (requests.get(f'{input_url}'))
soup = BeautifulSoup(text.text, 'html')
soup
pagination = soup.find('span', class_= 'total_pages')

if pagination:
    total_pages_text = pagination.text

    # Извлечем число из текст
    total_pages_match = re.search(r'\b(\d+)\b', total_pages_text)
    if total_pages_match:
         total_pages = int(total_pages_match.group(1))
total_pages

Необходимо указать заглавную страницу товарной категории: https://www.joytoy.com/collections/warhammer-action-figure


15

In [4]:
# Заданные переменные
page = 1
max_page = total_pages

# Список для хранения данных всех страниц
all_data = []

# Цикл для перебора страниц
for page in range(page, max_page + 1):
    url = f'{input_url}?page={page}'   #указываем юрл категории
    text = requests.get(url)
    soup = BeautifulSoup(text.text, 'html.parser')

    # Обработка содержимого страницы
    elements = soup.find_all('div', class_='prod_info')

    all_data_page = []
    for e in elements:
        all_data_page.append({
            'name': e.find('a', class_='item_name themes_products_title').text.strip(),
            'price': e.find('div', class_='item_price themes_products_price').text.strip().replace('\n$', '').replace('$', ''),
            'href': e.find('a', class_='item_name themes_products_title')['href']
        })

    img_tags = soup.find_all('img', class_='lazyload transition2')

    data_image = []
    for img_tag in img_tags:
        img_data_srcset = img_tag['data-srcset']
        data_image.append({
            'img': img_data_srcset
        })

    df_page_number = pd.DataFrame(all_data_page)
    df_data_image = pd.DataFrame(data_image)

    df_merged = pd.concat([df_page_number, df_data_image], axis=1)
    all_data.append(df_merged)

# Объединяем данные всех страниц в один DataFrame
final_df = pd.concat(all_data, ignore_index=True)
# Результат
final_df
# Преобразуем DataFrame в строку
#df_str = final_df.to_string(max_colwidth=150)
#print(df_str)

name         price  \
0        Ultramarines Librarian in Terminator Armour    73.6 79.99   
1    Ultramarines Terminator Captain Severus Agemman   67.16 72.99   
2                      Ultramarines Terminator Squad  150.3 166.99   
3                               Blood Angels Veteran    117 129.99   
4               Space Marines Space Wolves Claw Pack    117 129.99   
..                                               ...           ...   
295                       Black Legion Brother Talas            65   
296                  Space Wolves Battle Hunter Pack         99.99   
297                        Invictor Tactical Warsuit        149.99   
298                        Ultramarines Infiltrators     65.79 129   
299                           Ultramarines Incursors     65.79 129   

                                                  href  \
0    /products/ultramarines-librarian-in-terminator...   
1    /products/ultramarines-terminator-captain-seve...   
2              /products/ultramarines-terminator-squad   
3                       /products/blood-angels-veteran   
4       /products/space-marines-space-wolves-claw-pack   
..                                                 ...   
295               /products/black-legion-brother-talas   
296          /products/space-wolves-battle-hunter-pack   
297                /products/invictor-tactical-warsuit   
298                /products/ultramarines-infiltrators   
299                   /products/ultramarines-incursors   

                                                   img  
0    https://img.joytoy.com/u_file/2404/04/products...  
1    https://img.joytoy.com/u_file/2404/04/products...  
2    https://img.joytoy.com/u_file/2404/04/products...  
3    https://img.joytoy.com/u_file/2404/03/products...  
4    https://img.joytoy.com/u_file/2403/25/products...  
..                                                 ...  
295  https://img.joytoy.com/u_file/2307/11/products...  
296  https://img.joytoy.com/u_file/2307/11/products...  
297  https://img.joytoy.com/u_file/2307/12/products...  
298  https://img.joytoy.com/u_file/2307/11/products...  
299  https://img.joytoy.com/u_file/2307/11/products...  

[300 rows x 4 columns]

## **Создаем столбец Card_link в итоговом датафрейме df_str**

In [5]:
site = 'https://www.joytoy.com'
final_df['card_link'] = site + final_df['href']
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
final_df

name  \
0                                          Ultramarines Librarian in Terminator Armour   
1                                      Ultramarines Terminator Captain Severus Agemman   
2                                                        Ultramarines Terminator Squad   
3                                                                 Blood Angels Veteran   
4                                                 Space Marines Space Wolves Claw Pack   
5                      Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
6                           Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
7                                             Sons of Horus Justaerin Terminator Squad   
8                       Sons of Horus Legion Praetor in Cataphractii Terminator Armour   
9                                                    Sons of Horus MKIV Tactical Squad   
10                         Sons of Horus Contemptor Dreadnought with Gravis Autocannon   
11                                         Sons of Horus Legion Praetor with Power Axe   
12                                                   Sons of Horus MKVI Tactical Squad   
13       Adeptus Custodes Vexilus Praetor in Allarus Terminator Armour Phelam Tolguror   
14                               Adepta Sororitas Penitent Engine with Penitent Flails   
15                                               Imperial Fists Contemptor Dreadnought   
16                                 Imperial Fists Legion Cataphractii Terminator Squad   
17                                                                  Intercessors Group   
18                                        Adeptus Custodes Solar Watch Custodian Guard   
19                                                         Imperial Fists Intercessors   
20                                                           Blood Angels Intercessors   
21                                                           Ultramarines Intercessors   
22                                                           Space Wolves Intercessors   
23                       Imperial Fists Sigismund, First Captain of the lmperial Fists   
24                                           Imperial Fists Mklll Breacher Legionaries   
25                                                          Grey Knights Kaldor Draigo   
26                                                  Dark Angels Deathwing Knight Squad   
27                                                  Dark Angels Deathwing Strikemaster   
28                                                          Imperial Fists Fafnir Rann   
29                                      Imperial Fists Legion Praetor with Power Sword   
30                                          Imperial Fists Mklll Despoiler Legionaries   
31                                           Imperial Fists MkIII Tactical Legionaries   
32                                               Imperial Fists Legion Chaplain Consul   
33                                                           Grey Knights Strike Squad   
34                                                      Grey Knights Interceptor Squad   
35                                                     Adeptus Custodes Blade Champion   
36                       Adeptus Mechanicus Kastelan Robot with Heavy Phosphor Blaster   
37                                            Astra Militarum Cadian Armoured Sentinel   
38                                                       Ultramarines Primaris Captain   
39                                              Black Templars Primaris Sword Brethren   
40                                                    Adepta Sororitas Penitent Engine   
41                                                               Ultramarines Judiciar   
42                                                    Ultramarines Chaplain(Indomitus)   
43                                      Adepta Sororitas Abbess Sanctorum Morvenn Vahl   
44                            Im

## **Получения ДАТАФРЕЙМА вместе с SKU**


In [6]:
final_df['SKU'] = ''

for index, row_value in enumerate(final_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'

    # Отправляем запрос к URL
    text_card = requests.get(url)

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, например, значение атрибута sku
        div_tags = soup.find_all('div', class_='detail_sku')
        if div_tags:
            first_div_tag = div_tags[0]
            sku_value = first_div_tag.get('sku')

            # Сохраняем результат в final_df
            final_df.at[index, 'SKU'] = sku_value
        else:
            # Если тег с классом 'detail_sku' не найден, можно установить другое значение по умолчанию
            final_df.at[index, 'SKU'] = 'Not Found'
    else:
        # Если запрос не успешен, можно установить другое значение по умолчанию
        final_df.at[index, 'SKU'] = 'Request Failed'

# Выводим результаты
final_df.index.name = '№'
final_df
#print(final_df.to_string(index=False))

name  \
№                                                                                        
0                                          Ultramarines Librarian in Terminator Armour   
1                                      Ultramarines Terminator Captain Severus Agemman   
2                                                        Ultramarines Terminator Squad   
3                                                                 Blood Angels Veteran   
4                                                 Space Marines Space Wolves Claw Pack   
5                      Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
6                           Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
7                                             Sons of Horus Justaerin Terminator Squad   
8                       Sons of Horus Legion Praetor in Cataphractii Terminator Armour   
9                                                    Sons of Horus MKIV Tactical Squad   
10                         Sons of Horus Contemptor Dreadnought with Gravis Autocannon   
11                                         Sons of Horus Legion Praetor with Power Axe   
12                                                   Sons of Horus MKVI Tactical Squad   
13       Adeptus Custodes Vexilus Praetor in Allarus Terminator Armour Phelam Tolguror   
14                               Adepta Sororitas Penitent Engine with Penitent Flails   
15                                               Imperial Fists Contemptor Dreadnought   
16                                 Imperial Fists Legion Cataphractii Terminator Squad   
17                                                                  Intercessors Group   
18                                        Adeptus Custodes Solar Watch Custodian Guard   
19                                                         Imperial Fists Intercessors   
20                                                           Blood Angels Intercessors   
21                                                           Ultramarines Intercessors   
22                                                           Space Wolves Intercessors   
23                       Imperial Fists Sigismund, First Captain of the lmperial Fists   
24                                           Imperial Fists Mklll Breacher Legionaries   
25                                                          Grey Knights Kaldor Draigo   
26                                                  Dark Angels Deathwing Knight Squad   
27                                                  Dark Angels Deathwing Strikemaster   
28                                                          Imperial Fists Fafnir Rann   
29                                      Imperial Fists Legion Praetor with Power Sword   
30                                          Imperial Fists Mklll Despoiler Legionaries   
31                                           Imperial Fists MkIII Tactical Legionaries   
32                                               Imperial Fists Legion Chaplain Consul   
33                                                           Grey Knights Strike Squad   
34                                                      Grey Knights Interceptor Squad   
35                                                     Adeptus Custodes Blade Champion   
36                       Adeptus Mechanicus Kastelan Robot with Heavy Phosphor Blaster   
37                                            Astra Militarum Cadian Armoured Sentinel   
38                                                       Ultramarines Primaris Captain   
39                                              Black Templars Primaris Sword Brethren   
40                                                    Adepta Sororitas Penitent Engine   
41                                                               Ultramarines Judiciar   
42                                                    Ultramarines Chaplain(Indomitus)   
43                              

In [7]:
images = soup.find_all('div', class_='editor_txt ck-content themes_text_content')[0].find_all('img')

# Получить значения атрибута src для каждого изображения
src_values = [img['src'] for img in images]

# Вывести результат
#print(src_values)

my_string_src_values = ', '.join(src_values)
src_values_format = my_string_src_values.replace(', ', ' | ')
#print(src_values_format)

In [8]:
final_df['all_img_card'] = ''

for index, row_value in enumerate(final_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'

    # Отправляем запрос к URL
    text_card = requests.get(url)

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, например, значение атрибута src
        images = soup.find_all('div', class_='editor_txt ck-content themes_text_content')[0].find_all('img')
        if images:
            # для получения значений атрибута src для всех изображений
            img_values = [img.get('src') for img in images]
            my_string_src_values = ', '.join(img_values) # используем метод джоин для для перевода листа img_values в строку
            src_values_format = my_string_src_values.replace(', ', ' | ') # заменяем символ в строке
            # Сохраняем результат в final_df
            final_df.at[index, 'all_img_card'] = src_values_format
        else:
            # Если теги img не найдены, можно установить другое значение по умолчанию
            final_df.at[index, 'all_img_card'] = 'Not Found'
    else:
        # Если запрос не успешен, можно установить другое значение по умолчанию
        final_df.at[index, 'all_img_card'] = 'Request Failed'

# Выводим результаты
final_df.index.name = '№'
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
final_df

name  \
№                                                                                        
0                                          Ultramarines Librarian in Terminator Armour   
1                                      Ultramarines Terminator Captain Severus Agemman   
2                                                        Ultramarines Terminator Squad   
3                                                                 Blood Angels Veteran   
4                                                 Space Marines Space Wolves Claw Pack   
5                      Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
6                           Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
7                                             Sons of Horus Justaerin Terminator Squad   
8                       Sons of Horus Legion Praetor in Cataphractii Terminator Armour   
9                                                    Sons of Horus MKIV Tactical Squad   
10                         Sons of Horus Contemptor Dreadnought with Gravis Autocannon   
11                                         Sons of Horus Legion Praetor with Power Axe   
12                                                   Sons of Horus MKVI Tactical Squad   
13       Adeptus Custodes Vexilus Praetor in Allarus Terminator Armour Phelam Tolguror   
14                               Adepta Sororitas Penitent Engine with Penitent Flails   
15                                               Imperial Fists Contemptor Dreadnought   
16                                 Imperial Fists Legion Cataphractii Terminator Squad   
17                                                                  Intercessors Group   
18                                        Adeptus Custodes Solar Watch Custodian Guard   
19                                                         Imperial Fists Intercessors   
20                                                           Blood Angels Intercessors   
21                                                           Ultramarines Intercessors   
22                                                           Space Wolves Intercessors   
23                       Imperial Fists Sigismund, First Captain of the lmperial Fists   
24                                           Imperial Fists Mklll Breacher Legionaries   
25                                                          Grey Knights Kaldor Draigo   
26                                                  Dark Angels Deathwing Knight Squad   
27                                                  Dark Angels Deathwing Strikemaster   
28                                                          Imperial Fists Fafnir Rann   
29                                      Imperial Fists Legion Praetor with Power Sword   
30                                          Imperial Fists Mklll Despoiler Legionaries   
31                                           Imperial Fists MkIII Tactical Legionaries   
32                                               Imperial Fists Legion Chaplain Consul   
33                                                           Grey Knights Strike Squad   
34                                                      Grey Knights Interceptor Squad   
35                                                     Adeptus Custodes Blade Champion   
36                       Adeptus Mechanicus Kastelan Robot with Heavy Phosphor Blaster   
37                                            Astra Militarum Cadian Armoured Sentinel   
38                                                       Ultramarines Primaris Captain   
39                                              Black Templars Primaris Sword Brethren   
40                                                    Adepta Sororitas Penitent Engine   
41                                                               Ultramarines Judiciar   
42                                                    Ultramarines Chaplain(Indomitus)   
43                              

**ПАРСИНГ КАРТОЧЕК С РЯДОМ ПОЗИЦИЙ ВНТУРИ КАРТОЧКИ**

In [35]:
filtered_df = final_df[final_df['SKU'].str.contains('ZH', case=False)]
filtered_df

name          price  \
№                                                                        
2                         Ultramarines Terminator Squad   150.3 166.99   
3                                  Blood Angels Veteran     117 129.99   
4                  Space Marines Space Wolves Claw Pack     117 129.99   
7              Sons of Horus Justaerin Terminator Squad         229.99   
9                     Sons of Horus MKIV Tactical Squad         181.96   
12                    Sons of Horus MKVI Tactical Squad         171.96   
16  Imperial Fists Legion Cataphractii Terminator Squad         231.96   
17                                   Intercessors Group          99.96   
18         Adeptus Custodes Solar Watch Custodian Guard         137.97   
24            Imperial Fists Mklll Breacher Legionaries  129.99 139.99   
26                   Dark Angels Deathwing Knight Squad  175.99 191.99   
27                   Dark Angels Deathwing Strikemaster  179.99 195.99   
30           Imperial Fists Mklll Despoiler Legionaries    79.99 87.99   
31            Imperial Fists MkIII Tactical Legionaries  166.99 181.99   
33                            Grey Knights Strike Squad         139.99   
34                       Grey Knights Interceptor Squad         139.99   
39               Black Templars Primaris Sword Brethren         128.97   
46                       Ultramarines Desolation Marine     126 139.99   
49            Primaris Space Marines Bladeguard Veteran         171.96   

                                                               href  \
№                                                                     
2                           /products/ultramarines-terminator-squad   
3                                    /products/blood-angels-veteran   
4                    /products/space-marines-space-wolves-claw-pack   
7                /products/sons-of-horus-justaerin-terminator-squad   
9                       /products/sons-of-horus-mkiv-tactical-squad   
12                      /products/sons-of-horus-mkvi-tactical-squad   
16    /products/imperial-fists-legion-cataphractii-terminator-squad   
17                                           /products/intercessors   
18           /products/adeptus-custodes-solar-watch-custodian-guard   
24              /products/imperial-fists-mklll-breacher-legionaries   
26                     /products/dark-angels-deathwing-knight-squad   
27                    /products/dark-angels-deathwing-action-figure   
30             /products/imperial-fists-mklll-despoiler-legionaries   
31               /products/imperial-fists-mklli-tacticallegionaries   
33                              /products/grey-knights-strike-squad   
34                         /products/grey-knights-interceptor-squad   
39                 /products/black-templars-primaris-sword-brethren   
46  /products/ultramarines-desolation-sergeant-with-vengor-launcher   
49              /products/primaris-space-marines-bladeguard-veteran   

                                                                                                                         img  \
№                                                                                                                              
2   https://img.joytoy.com/u_file/2404/04/products/c86d06dd31.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
3   https://img.joytoy.com/u_file/2404/03/products/6a0ebc7628.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
4   https://img.joytoy.com/u_file/2403/25/products/ba4c491422.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
7   https://img.joytoy.com/u_file/2403/05/products/ece4668001.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
9   https://img.joytoy.com/u_file/2402/29/products/19be8268da.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
12  https://img.joytoy.com/u_file/2402/15/products/b9d8c69a59.jpg?x-oss-process=image/quality,q_80/resize,m_

In [89]:
#url2 = 'https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114'
for index, row_value in enumerate(filtered_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'
    response = requests.get(url)

    if response.status_code == 200:
      soup = BeautifulSoup(response.text, 'html.parser')

    # Находим все элементы input с id='ext_attr'
    attr_box_elements = soup.find_all('input', id='ext_attr')

    # Проверяем, найдены ли элементы
    if attr_box_elements:
        # Проходимся по всем найденным элементам
        for attr_box_element in attr_box_elements:
            # Получаем значение атрибута value
            value = attr_box_element.get('value')

            # Декодируем HTML-сущности в строке
            decoded_value = decode_html_entities(value)

            try:
                # Преобразуем строку в объект Python (словарь)
                data = json.loads(decoded_value)

                # Выводим полученные данные
                print(data)
            except json.JSONDecodeError as e:
                print("Ошибка при разборе JSON:", e)
    else:
        print("Элементы с id='ext_attr' не найдены.")

{'Total': {'set of 3': [['166.99', '198', '1.05', 'ZH233047', '0.00', '4142', '10126', '0', '1']], 'Sergeant with Power Sword and Teleport Homer': [['57.99', '197', '0.35', '6973130379923', '0.00', '4144', '10127', '0', '0']], 'Terminator with Storm Bolter': [['54.99', '199', '0.35', '6973130379930', '0.00', '4150', '10128', '0', '0']], 'Terminator with Assault Cannon': [['54.99', '198', '0.35', '6973130379947', '0.00', '4156', '10129', '0', '0']]}}
{'Total': {'SET OF 4': [['129.99', '98', '1.4', 'ZH72899602', '0.00', '4084', '10114', '0', '1']], 'Laenatus': [['32.99', '100', '0.35', '6973130373402', '0.00', '4086', '10115', '0', '0']], 'Vigna': [['32.99', '99', '0.35', '6973130373396', '0.00', '4091', '10116', '0', '0']], 'Salus': [['32.99', '100', '0.35', '6973130373389', '0.00', '4096', '10117', '0', '0']], 'Alberigo': [['32.99', '96', '0.35', '6973130373372', '0.00', '4101', '10118', '0', '0']]}}
{'Total': {'Set of 4': [['129.99', '92', '1.4', 'ZH02192633', '0.00', '3987', '10095',

In [39]:
for index, row_value in enumerate(filtered_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = row_value

    urls = []

    # Отправляем запрос к URL
    response = requests.get(url)

    # Проверяем успешность запроса
    if response.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(response.text, 'html.parser')

        # Ищем тег <meta> с атрибутом property="og:url"
        meta_tag = soup.find('meta', property='og:url')

        # Проверяем, найден ли тег
        if meta_tag:
            # Получаем содержимое атрибута content
            url_content = meta_tag.get('content')

            # Добавляем URL в список результатов
            urls.append(url_content)

# Выводим список URL
urls

['https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran']

In [42]:
meta_tag

<meta content="https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran" property="og:url"/>

In [81]:
data = {
    'card_link': ['https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114', 'https://www.joytoy.com/products/ultramarines-terminator-squad?VariantsId=10126', 'https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran?VariantsId=10009'],
    # добавьте другие столбцы, если необходимо
}

# Создание DataFrame
final_df2 = pd.DataFrame(data)

final_df2

card_link
0                       https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114
1              https://www.joytoy.com/products/ultramarines-terminator-squad?VariantsId=10126
2  https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran?VariantsId=10009

In [ ]:
final_df2['SET_CNT'] = ''

for index, row_value in enumerate(final_df2['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'

    # Отправляем запрос к URL
    text_card = requests.get(url)

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, значение атрибута, value
        attr_box_element = soup.find_all('div', class_='btn_attr GoodBorderColor GoodBorderHoverColor')
        if attr_box_element in attr_box_element:
          value =  attr_box_element['value']
          set_value = first_div_tag.get('value')
          # Сохраняем результата в столбец
          final_df2.at[index, 'SET_CNT'] = set_value


In [83]:
final_df2

card_link  \
0                       https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114   
1              https://www.joytoy.com/products/ultramarines-terminator-squad?VariantsId=10126   
2  https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran?VariantsId=10009   

  SET_CNT  
0          
1          
2

In [12]:
pd.final_df2 = [card_link:'https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114', 'https://www.joytoy.com/products/ultramarines-terminator-squad?VariantsId=10126,' 'https://www.joytoy.com/products/ultramarines-terminator-captain-severus-agemman']
final_df2

SyntaxError: invalid syntax (<ipython-input-12-23d22322d8fe>, line 1)

In [ ]:
final_df2 = final_df2[['card_link']]

In [64]:
url2 = 'https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114'
response = requests.get(url2)
if response.status_code == 200:
  html_content = response.text
  soup = BeautifulSoup(html_content, 'html.parser')
attr_box_elements = soup.find_all('input', id= 'ext_attr')

attr_box_elements

[<input id="ext_attr" type="hidden" value='{"Total":{"SET OF 4":[["129.99","98","1.4","ZH72899602","0.00","4084","10114","0","1"]],"Laenatus":[["32.99","100","0.35","6973130373402","0.00","4086","10115","0","0"]],"Vigna":[["32.99","99","0.35","6973130373396","0.00","4091","10116","0","0"]],"Salus":[["32.99","100","0.35","6973130373389","0.00","4096","10117","0","0"]],"Alberigo":[["32.99","96","0.35","6973130373372","0.00","4101","10118","0","0"]]}}'/>]

In [75]:
total_data = data.get('Total', {})

# Проходимся по каждому элементу внутреннего словаря 'Total'
for key, value in total_data.items():
    # В value у нас список списков. Первый элемент каждого списка содержит цену
    #prices = [item[0] for item in value]
    first_three_values = [item[:7] for item in value]
    print(f"'{key}': {first_three_values}")

'SET OF 4': [['129.99', '98', '1.4', 'ZH72899602', '0.00', '4084', '10114']]
'Laenatus': [['32.99', '100', '0.35', '6973130373402', '0.00', '4086', '10115']]
'Vigna': [['32.99', '99', '0.35', '6973130373396', '0.00', '4091', '10116']]
'Salus': [['32.99', '100', '0.35', '6973130373389', '0.00', '4096', '10117']]
'Alberigo': [['32.99', '96', '0.35', '6973130373372', '0.00', '4101', '10118']]


In [88]:
total_data = data.get('Total', {})

# Проходимся по каждому элементу внутреннего словаря 'Total'
for key, value in total_data.items():
    # В value у нас список списков. Первый элемент каждого списка содержит цену
    #prices = [item[0] for item in value]
    first_three_values = [item[:7] for item in value]
    print(f"'{key}': {first_three_values}")

'Space Wolve Bladeguard Veteran': [['42.99', '26', '0.35', '6973130372795', '0.00', '3016', '10009']]
'Imperial Fists Bladeguard Veteran': [['42.99', '30', '0.35', '6973130372771', '0.00', '3022', '10010']]
'Blood Angels Bladeguard Veteran': [['42.99', '21', '0.35', '6973130372788', '0.00', '3028', '10011']]
'Black TemplarsBladeguard Veteran': [['42.99', '26', '0.35', '6973130372801', '0.00', '3034', '10012']]
'Bladeguard Veteran 4-piece set': [['171.96', '23', '1.4', 'ZH71889501', '0.00', '3014', '10013']]


In [ ]:
СОЗДАЕМ ДАТАФРЕЙМ С ЭТИМИ ЗНАЧЕНИЯМ ПЕРЕД СОЗДАНИЕМ И ПАРСИНГА ССЫЛКИ

In [55]:
for attr_box_element in attr_box_element:
    value =  attr_box_element['value']
    print(value)
    break

KeyError: 'value'

In [52]:
url2 = 'https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran'
response = requests.get(url2)
if response.status_code == 200:
  html_content = response.text
  soup = BeautifulSoup(html_content, 'html.parser')
input_element = soup.find_all('div', class_ = 'ext_attr')
if input_element:
  # Получаем значение атрибута value
  value = input_element.get('value')
  # Декодируем HTML-сущности в строке
  decoded_value = decode_html_entities(value)
  # Преобразуем строку в объект Python (словарь)
  data = json.loads(decoded_value)
  # Выводим полученные данные
  print(data)

In [31]:
###Получение последнего символа

attr_box_list = list(attr_box_element)

if attr_box_element:
    # Получаем значение 'value' первого элемента
    value = attr_box_element[0]['value']
    words = value.split()
    last_word2 = words[-1]
else:
    print("Список attr_box_element пуст")

KeyError: 0

In [ ]:
#Получение последнего значения

words = value.split()

# Получение последнего слова
last_word = words[-1]

last_word

#  ФОРМИРОВАНИЕ ФАЙЛОВ ДЛЯ ИМПОРТА В КАБИНЕТЫ АВИТО И ВК

## **--> ФОРМИРОВАНИЕ ФАЙЛОВ ДЛЯ АВИТО**

**Создаем таблицу для загрузки в АВИТО**

In [ ]:
#Создаем ключевые столбцы из парсинга датафрейма
avit_df = final_df[['SKU', 'name', 'all_img_card']]
avit_df[:5]

SKU  \
№                  
0     ZH02192633   
1  6973130379770   
2  6973130379787   
3     ZH18253249   
4  6973130379619   

                                                              name  \
№                                                                    
0                             Space Marines Space Wolves Claw Pack   
1  Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
2       Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
3                         Sons of Horus Justaerin Terminator Squad   
4   Sons of Horus Legion Praetor in Cataphractii Terminator Armour   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                all_img_card  
№                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
0                                                                                                                            https://img.joytoy.com/u_file/2403/25/photo/1-3.jpg | https://img.joytoy.com/u_file/2403/25/photo/2.jpg | https://img.joytoy.com/u_file/2403/25/photo/7.jpg | https://img.joytoy.com/u_file/2403/25/photo/4.jpg | https://img.joytoy.com/u_file/2403/25/photo/6.jpg | https://img.joytoy.com/u_file/2403/25/photo/8.jpg | https://img.joytoy.com/u_file/24

**Задачем столбцы со статичными значениями**

In [ ]:
Description_string = """
В нaличии. Hовый, запечатанный.

JоyТоy {name}

Oчeнь мнoго пoдвижныx суставов, сoответcтвeннo бoльшой выбop пoз для фигурки - к каждой мoдeли идут дополнительные головы, руки, оружие и т.д.

❤️ Добавь это объявление к себе в избранное

✅ В профиле есть еще очень много интересного!)

Если интересует что-то из Jоytоy Wаrhаmmеr/Infinity/Dаrk Sоursе/LЕGО, пишите - можем привезти под заказ!

# Wаrhаmmеr 40000, Вархаммер 40000, Wаrhаmmеr 40k, JоyТоy, Jоy Тоy, Dеаth Коrрs оf Кriеg, Корпус Смерти Крига, Имперская гвардия, Imреriаl Guаrd, Sрасе Маrinеs, Sрасе Wоlvеs, Ultrаmаrinеs, Ультрамарины, Вlооd Аngеls, Кровавые Ангелы, Аstrа Мilitаrum, Ваха, Коллекционные фигурки"""

#Description_string

#display(avit_df.style.set_properties(subset=[Description_string'], **{'white-space': 'pre-line'}))

In [ ]:
avit_df['AvitoId'], avit_df['AdStatus'], avit_df['Category'], avit_df['GoodsType'],  avit_df['VehicleType'], avit_df['Address'], avit_df['Condition'], avit_df['AdType'], avit_df['ContactPhone'], avit_df['DateBegin'], avit_df['DateEnd'], avit_df['AllowEmail'], avit_df['ManagerName'], avit_df['ImageNames'], avit_df['Description'], avit_df['Price'] = '', 'Free', 'Коллекционирование', 'Модели', '', 'Москва, метро Улица Скобелевская', 'Новое', 'Продаю своё', '+7 985 182-56-36', '', '', '', '', '', Description_string, ''

<ipython-input-30-d66c6d39393a>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  avit_df['AvitoId'], avit_df['AdStatus'], avit_df['Category'], avit_df['GoodsType'],  avit_df['VehicleType'], avit_df['Address'], avit_df['Condition'], avit_df['AdType'], avit_df['ContactPhone'], avit_df['DateBegin'], avit_df['DateEnd'], avit_df['AllowEmail'], avit_df['ManagerName'], avit_df['ImageNames'], avit_df['Description'], avit_df['Price'] = '', 'Free', 'Коллекционирование', 'Модели', '', 'Москва, метро Улица Скобелевская', 'Новое', 'Продаю своё', '+7 985 182-56-36', '', '', '', '', '', Description_string, ''
<ipython-input-30-d66c6d39393a>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,

In [ ]:
avit_df[:2]

SKU  \
№                  
0     ZH02192633   
1  6973130379770   

                                                              name  \
№                                                                    
0                             Space Marines Space Wolves Claw Pack   
1  Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      all_img_card  \
№                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
0  https://img.joytoy.com/u_file/2403/25/photo/1-3.jpg | https://img.joytoy.com/u_file/2403/25/photo/2.jpg | https://img.joytoy.com/u_file/2403/25/photo/7.jpg | https://img.joytoy.com/u_file/2403/25/photo/4.jpg | https://img.joytoy.com/u_file/2403/25/photo/6.jpg | https://img.joytoy.com/u_file/2403/25/photo/8.jpg | https://img.joytoy.com/u_file/2403/25/photo/4-845c.jpg | https://img.joytoy.com/u_file/2403/25/photo/7-1c07.jpg | https://img.joytoy.com/u_file/2403/25/photo/2-d5ef.jpg | https://img.joytoy.com/u_file/2403/25/photo/5.jpg | https://img.joytoy.com/u_file/2403/25/photo/6-e6d4.jpg | https://img.joytoy.com/u_file/2403/25/photo/8-6603.jpg | https://img.joytoy.com/u_file/2403/25/photo/2-7a24.jpg | https://img.joytoy.com/u_file/2403/25/photo/3.jpg | https://img.joytoy.com/u_file/2403/25/photo/4-7799.jpg | https://img.joytoy.com/u_file/2403/25/photo/5-96e8.jpg | https://img.joytoy.com/u_file/2403/25/photo/7-6635.jpg | https://img.joytoy.com/u_file/2403/25/photo/8-3a6

In [ ]:
# заменяем в столбце Description заглушку {name} на значение товара из столбца name
def replace_name(row):
    return row['Description'].replace('{name}', row['name'])

avit_df['Description'] = avit_df.apply(replace_name, axis=1)

In [ ]:
avit_df

SKU  \
№                     
0        ZH02192633   
1     6973130379770   
2     6973130379787   
3        ZH18253249   
4     6973130379619   
5        ZH02968972   
6     6973130379510   
7     6973130379503   
8        ZH66738097   
9     6973130373938   
10    6973130379442   
11    6973130379411   
12       ZH74819804   
13       ZH32495625   
14         ZH364350   
15    6973130376656   
16    6973130376649   
17    6973130376632   
18    6973130376625   
19    6973130379237   
20      ZH107114121   
21    6973130379220   
22         ZH900613   
23         ZH697683   
24    6973130379145   
25    6973130379138   
26       ZH90849091   
27       ZH46536077   
28    6973130379039   
29         ZH950815   
30         ZH647188   
31    6973130378124   
32    6973130378957   
33    6973130378940   
34    6973130373297   
35         ZH462239   
36    6973130378889   
37    6973130378896   
38    6973130378902   
39    6973130378872   
40    6973130378865   
41    6973130378834   
42         ZH031027   
43   6973130378841    
44    6973130378858   
45       ZH71889501   
46    6973130378032   
47    6973130378025   
48    6973130378018   
49    6973130378155   
50    6973130378148   
51    6973130378131   
52    6973130376502   
53    6973130377325   
54    6973130377585   
55    6973130377981   
56    6973130377974   
57    6973130377967   
58    6973130377943   
59    6973130377936   
60    6973130377929   
61    6973130377912   
62    6973130377905   
63    6973130377899   
64    6973130377882   
65    6973130377844   
66    6973130377851   
67    6973130377868   
68    6973130372337   
69    6973130372344   
70    6973130372351   
71    6973130377790   
72    6973130377837   
73    6973130377820   
74    6973130377813   
75    6973130377806   
76    6973130377783   
77    6973130377745   
78    6973130377738   
79    6973130377721   
80    6973130377752   
81    6973130377714   
82    6973130377691   
83    6973130377684   
84    6973130377677   
85    6973130376434   
86    6973130377592   
87    6973130377530   
88    6973130376878   
89    6973130376885   
90    6973130376861   
91    6973130376854   
92    6973130376847   
93    6973130376816   
94    6973130376809   
95    6973130376793   
96    6973130376717   
97    6973130376700   
98    6973130376694   
99    6973130376687   
100   6973130376670   
101   6973130376663   
102   6973130376533   
103   6973130376496   
104   6973130376519   
105   6973130376526   
106   6973130376557   
107   6973130376540   
108   6973130376489   
109   6973130376465   
110   6973130376458   
111   6973130376441   
112   6973130376427   
113   6973130373587   
114   6973130376335   
115   6973130376342   
116   6973130375550   
117   6973130375543   
118   6973130375536   
119   6973130375529   
120   6973130375512   
121   6973130375505   
122   6973130375567   
123   6973130375376   
124   6973130375369   
125   6973130375352   
126   6973130375338   
127   6973130375277   
128   6973130375260   
129   6973130375253   
130   6973130375246   
131   6973130375239   
132   6973130375222   
133   6973130375215   
134   6973130375321   
135   6973130375314   
136   6973130375284   
137   6973130375307   
138   6973130375208   
139   6973130375161   
140   6973130375154   
141   6973130375147   
142   6973130375130   
143   6973130375123   
144   6973130375048   
145   6973130375031   
146   6973130375024   
147   6973130375017   
148   6973130375000   
149   6973130375086   
150   6973130375079   
151   6973130375062   
152   6973130374966   
153   6973130374959   
154   6973130374942   
155   6973130374935   
156   6973130374867   
157   6973130374850   
158   6973130374843   
159   6973130374768   
160   6973130374782   
161   6973130374775   
162   6973130372474   
163   6973130372498   
164   6973130374553   
165   6973130374546   
166   6973130374607   
167   6973130374591   
168   6973130374584   
169   6973130374577   
170   6973130374638   
171   6973130374621   
172   69731303

In [ ]:
# Выполняем переименование столбцов под требования шаблона
new_column_name = ['Id', 'Title', 'ImageUrls']
old_column_name = ['SKU', 'name', 'all_img_card'] # имя столбца, которое вы хотите изменить
avit_df.rename(columns=dict(zip(old_column_name, new_column_name)), inplace=True)

In [ ]:
# Функция для оставления части строки по количеству вхождения символа
def keep_part_by_char_count(string, char, count):
    # Ищем индексы вхождений символа
    indices = [i for i, c in enumerate(string) if c == char]
    if len(indices) < count:
        return string
    else:
        return string[:indices[count-1]+1]

# Применяем функцию к определенным строкам в столбце 'text'
char = '|'
count = 9
avit_df['ImageUrls'] = avit_df['ImageUrls'].apply(lambda x: keep_part_by_char_count(x, char, count))

In [ ]:
# Выводим столбцы в порядке шаблона
avit_df_final = avit_df[['Id', 'AvitoId', 'AdStatus', 'Category', 'GoodsType', 'VehicleType', 'Address', 'Title', 'Description', 'Condition', 'Price', 'AdType', 'DateBegin', 'DateEnd', 'AllowEmail', 'ManagerName', 'ContactPhone', 'ImageNames', 'ImageUrls']]
avit_df_final

Id AvitoId AdStatus            Category GoodsType  \
№                                                                    
0        ZH02192633             Free  Коллекционирование    Модели   
1     6973130379770             Free  Коллекционирование    Модели   
2     6973130379787             Free  Коллекционирование    Модели   
3        ZH18253249             Free  Коллекционирование    Модели   
4     6973130379619             Free  Коллекционирование    Модели   
5        ZH02968972             Free  Коллекционирование    Модели   
6     6973130379510             Free  Коллекционирование    Модели   
7     6973130379503             Free  Коллекционирование    Модели   
8        ZH66738097             Free  Коллекционирование    Модели   
9     6973130373938             Free  Коллекционирование    Модели   
10    6973130379442             Free  Коллекционирование    Модели   
11    6973130379411             Free  Коллекционирование    Модели   
12       ZH74819804             Free  Коллекционирование    Модели   
13       ZH32495625             Free  Коллекционирование    Модели   
14         ZH364350             Free  Коллекционирование    Модели   
15    6973130376656             Free  Коллекционирование    Модели   
16    6973130376649             Free  Коллекционирование    Модели   
17    6973130376632             Free  Коллекционирование    Модели   
18    6973130376625             Free  Коллекционирование    Модели   
19    6973130379237             Free  Коллекционирование    Модели   
20      ZH107114121             Free  Коллекционирование    Модели   
21    6973130379220             Free  Коллекционирование    Модели   
22         ZH900613             Free  Коллекционирование    Модели   
23         ZH697683             Free  Коллекционирование    Модели   
24    6973130379145             Free  Коллекционирование    Модели   
25    6973130379138             Free  Коллекционирование    Модели   
26       ZH90849091             Free  Коллекционирование    Модели   
27       ZH46536077             Free  Коллекционирование    Модели   
28    6973130379039             Free  Коллекционирование    Модели   
29         ZH950815             Free  Коллекционирование    Модели   
30         ZH647188             Free  Коллекционирование    Модели   
31    6973130378124             Free  Коллекционирование    Модели   
32    6973130378957             Free  Коллекционирование    Модели   
33    6973130378940             Free  Коллекционирование    Модели   
34    6973130373297             Free  Коллекционирование    Модели   
35         ZH462239             Free  Коллекционирование    Модели   
36    6973130378889             Free  Коллекционирование    Модели   
37    6973130378896             Free  Коллекционирование    Модели   
38    6973130378902             Free  Коллекционирование    Модели   
39    6973130378872             Free  Коллекционирование    Модели   
40    6973130378865             Free  Коллекционирование    Модели   
41    6973130378834             Free  Коллекционирование    Модели   
42         ZH031027             Free  Коллекционирование    Модели   
43   6973130378841              Free  Коллекционирование    Модели   
44    6973130378858             Free  Коллекционирование    Модели   
45       ZH71889501             Free  Коллекционирование    Модели   
46    6973130378032             Free  Коллекционирование    Модели   
47    6973130378025             Free  Коллекционирование    Модели   
48    6973130378018             Free  Коллекционирование    Модели   
49    6973130378155             Free  Коллекционирование    Модели   
50    6973130378148             Free  Коллекционирование    Модели   
51    6973130378131             Free  Коллекционирование    Модели   
52    6973130376502             Free  Коллекционирование    Модели   
53    6973130377325             Free  Коллекционирование    Модели   
54    6973130377585             Free  Коллекционирование    Модели   
55    6973130377981        

**СОХРАНЯЕМ ФАЙЛ ЭКСЕЛЬ**

In [ ]:
file_path = r"C:\Users\Fibo\Проекты\WH40\avito_df.xlsx"

avit_df_final.to_excel(file_path, index=False)

## --> ФОРМИРОВАНИЕ ФАЙЛОВ ДЛЯ ВК

In [ ]:
object_string = """
      <offer id="6973130379572" available="true">
        <price>3500</price>
        <count>0</count>
        <currencyId>RUB</currencyId>
        <name>Sons of Horus MKIV Sergeant with Power Fist</name>
        <description>Sons of Horus MKIV Sergeant with Power Fist</description>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7489.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7493.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7494.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7539.jpg</picture>
"""

In [ ]:
object_string

'\n      <offer id="6973130379572" available="true">\n        <price>3500</price>\n        <count>0</count>\n        <currencyId>RUB</currencyId>\n        <name>Sons of Horus MKIV Sergeant with Power Fist</name>\n        <description>Sons of Horus MKIV Sergeant with Power Fist</description>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7489.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7493.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7494.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7539.jpg</picture>\n'

In [ ]:
# Получаем шаблон YAML файла созданного бородой для ВК

file_path = "/content/VK_19.03.xml" # шаблон предварительно был загружен в каталог колаба в разелел файлов

with open (file_path) as f:
    data = f.read(1500) #вывод количества символов
print(data)

<?xml version="1.0" encoding="utf-8"?>
<yml_catalog date="2021-04-01 12:20">
  <shop>
    <name>JoyToy - Warhammer 40000, Dark Source, Infinity</name>
    <company>JoyToy - Warhammer 40000, Dark Source, Infinity</company>
    <url>https://vk.com/joytoy40k/</url>
    <currencies>
      <currency id="RUB" rate="1"/>
    </currencies>
    <categories>
      <category id="11">Warhammer 400001</category>
      <category id="2">Dark Source</category>
      <category id="3">В наличии</category>
      <category id="4">Предзаказ</category>
    </categories>
    <offers>
      <offer id="6973130379572" available="true">
        <price>3500</price>
        <count>0</count>
        <currencyId>RUB</currencyId>
        <name>Sons of Horus MKIV Sergeant with Power Fist</name>
        <description>Sons of Horus MKIV Sergeant with Power Fist</description>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262